In [1]:
import os

In [2]:
%pwd

'c:\\Users\\nikhil\\OneDrive\\Desktop\\ML Projects\\ipp\\research'

In [3]:
os.chdir("../")

In [4]:
%pwd

'c:\\Users\\nikhil\\OneDrive\\Desktop\\ML Projects\\ipp'

In [5]:
from dataclasses import dataclass
from pathlib import Path

In [6]:
@dataclass(frozen=True)
class ModelPredictionConfig:
    root_dir : Path
    preprocessor_obj_file_path : Path
    model_path : Path

In [7]:
from insurancePP.logging import logger
from insurancePP.utils.common import read_yaml, create_directories, load_object
from insurancePP.constants import *

In [8]:
class ConfigurationManager:
    def __init__(self, config_filepath = CONFIG_FILE_PATH, params_filepath = PARAMS_FILE_PATH):
        self.config = read_yaml(config_filepath)
        self.params = read_yaml(params_filepath)
        create_directories([self.config.artifacts_root])

    def get_model_prediction_config(self) -> ModelPredictionConfig:
        config = self.config.model_prediction
        create_directories([config.root_dir])

        return ModelPredictionConfig(
            root_dir = config.root_dir,
            preprocessor_obj_file_path = config.preprocessor_obj_file_path,
            model_path = config.model_path
        )

In [9]:
class ModelPrediction:
    def __init__(self, config : ModelPredictionConfig):
        self.config = config
        
    def predict_sample_data(self, data):
        preprocessor = load_object(self.config.preprocessor_obj_file_path)
        model = load_object(self.config.model_path)

        logger.info("Both preprocessor and model are loaded successfully from disk")
        return model.predict(preprocessor.transform(data))

In [10]:
import pandas as pd
sample = pd.DataFrame({'age':[19], 'sex':['female'], 'bmi':[27.9], 'children':[0], 'smoker':['yes'], 'region':['southwest']})

In [11]:
sample.dtypes

age           int64
sex          object
bmi         float64
children      int64
smoker       object
region       object
dtype: object

In [12]:
try:
    config = ConfigurationManager()
    model_prediction_config = config.get_model_prediction_config()
    model_prediction = ModelPrediction(config = model_prediction_config)
    result = model_prediction.predict_sample_data(sample)
    print(result)
    
except Exception as e:
    raise e

[2024-02-27 20:16:02,081 : INFO : common : yaml file: config\config.yaml loaded successfully]
[2024-02-27 20:16:02,086 : INFO : common : yaml file: params.yaml loaded successfully]
[2024-02-27 20:16:02,089 : INFO : common : directory artifacts created]
[2024-02-27 20:16:02,092 : INFO : common : directory artifacts/model_prediction created]


[2024-02-27 20:16:03,269 : INFO : 82938115 : Both preprocessor and model are loaded successfully from disk]
[18381.42742799]
